# Trader Joe's NYC Location Analysis

### By: Logan Chalifour

## Instructions

Where in New York City would you advise Trader Joe’s to open their next store?

## Import Packages

We start by importing some packages needed for our analysis.

In [ ]:
import numpy as np
import pandas as pd
import geopandas as gpd
import re
import json
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
from sklearn.preprocessing import MinMaxScaler

## Define Functions

We define some functions that we will use throughout our notebook. The nyc-zip-code-tabulation-areas-polygons.geojson file is sourced from a repo on GitHub. Explanations of the code can be found inline.

In [ ]:
# NYC and Manhattan center point used for plots
nyc_center={'lat': 40.710, 'lon': -73.985}
man_center={'lat': 40.785, 'lon': -73.971}

# Function for extracting coordinates from georeference point column
def extract_coordinates(georeference): # Example format: 'POINT (-73.71744 40.74408)'
    lat_lon = georeference.replace('POINT (', '').replace(')', '').split() # Replace and split
    return float(lat_lon[1]), float(lat_lon[0]) # Return latitude first, then longitude

# Function to find wildcard match using regex
def wildcard_match(pattern, string): # Pass pattern to and string to search for 
    return bool(re.search(pattern, string, flags=re.IGNORECASE)) # Search with case ignored

# Function to make plot of individual stores
def make_store_plot(df, title, opacity=1, color_column=None, color=None, center=nyc_center, zoom=10, save=False):
    
    # If to be saved
    if save == True:
        zoom = 10.5
    
    # Create a plot of stores with coordinates
    fig = px.scatter_mapbox(
        df,
        lat='Latitude',
        lon='Longitude',
        hover_name='DBA Name',
        hover_data={'Address': True, 'License Number': True, 'Type': True, 'Chain': True},
        mapbox_style='carto-positron'
    )

    # Multi-color
    if color_column is not None:
        color_discrete_map = {
            'SMALL': '#0288D1', # Blue
            'LARGE CHAIN': '#66BB6A', # Green
            'TRADER JOE\'S': '#EF5350' # Red
        }
        fig.update_traces(marker=dict(color=df[color_column].map(color_discrete_map)))
    
    # One color passed
    elif color is not None:
        fig.update_traces(marker=dict(color=color)) # User color

    # Default coloring
    else:
        fig.update_traces(marker=dict(color='#0288D1')) # Blue

    # Update point size and opacity
    fig.update_traces(marker=dict(size=5, opacity=opacity), selector=dict(mode='markers'))

    # Set the aspect ratio and formatting
    fig.update_layout(
        title=title,
        mapbox=dict(style='carto-positron', zoom=zoom, center=center),
        autosize=True,
        margin={"r":0,"t":0,"l":0,"b":0}
    )

    # Save the plot
    if save == True:
        pio.write_image(fig, 'stores_fullscreen.png', width=1920, height=1080)

    # Show the plot
    elif save == False:
        fig.show()

# Create zip code plot with stores overlayed
def make_zip_plot(df, stat_column, store_df=None, subway_df=None, center=nyc_center, zoom=10, save=False):
    # Load the GeoJSON file with zip code boundaries
    with open('nyc-zip-code-tabulation-areas-polygons.geojson') as file:
        geojson_data = json.load(file)

    # If to be saved
    if save == True:
        zoom = 10.5

    # If final recommendation plot
    if stat_column == 'Weighted Location Score':
        hover = ['Borough', 'Score | Population per Store', '2023 Population per Store', 'Score | Population per Chain', '2023 Population per Chain', 'Score | Population Growth Rate', '2-year Population Growth Rate', 'Weighted Location Score']

    else:
        hover = ['Zip Code', 'Borough', stat_column]

    # Create a choropleth map of the zip code data
    fig = px.choropleth_mapbox(
        df,
        geojson=geojson_data,
        locations='Zip Code',
        featureidkey='properties.postalCode',
        color=stat_column,
        color_continuous_scale='YlOrRd',
        center=center,
        mapbox_style='carto-positron',
        zoom=zoom,
        opacity=.3,
        labels={stat_column: stat_column},
        title=f'{stat_column} by Zip Code',
        hover_data=hover
    )

    # IF plotting stores too
    if store_df is not None:
        # Add store locations as scatter plot
        fig.add_trace(
            go.Scattermapbox(
                lat=store_df['Latitude'],
                lon=store_df['Longitude'],
                mode='markers',
                marker=dict(
                    size=8,
                    color='#EF5350',  # Red
                    opacity=1
                ),
                hoverinfo='text',
                customdata=store_df[['DBA Name', 'Address', 'License Number', 'Latitude', 'Longitude']],
                hovertemplate=
                    "DBA Name: %{customdata[0]}<br>"
                    "Address: %{customdata[1]}<br>" +
                    "License Number: %{customdata[2]}<br>" +
                    "Latitude: %{customdata[3]}<br>" +
                    "Longitude: %{customdata[4]}<br>",
                showlegend=False,
                name='Store'
            )
        )

    # If plotting subways too
    if subway_df is not None:
        # Add subway locations as scatter plot
        fig.add_trace(
            go.Scattermapbox(
                lat=subway_df['Latitude'],
                lon=subway_df['Longitude'],
                mode='markers',
                marker=dict(
                    size=4,
                    color='black',  # Black
                    opacity=1
                ),
                hoverinfo='text',
                customdata=subway_df[['NAME', 'LINE', 'NOTES', 'Latitude', 'Longitude']],
                hovertemplate=
                    "Name: %{customdata[0]}<br>" +
                    "Line: %{customdata[1]}<br>" +
                    "Notes: %{customdata[2]}<br>" +
                    "Latitude: %{customdata[3]}<br>" +
                    "Longitude: %{customdata[4]}<br>",
                showlegend=False,
                name='Subway Stop'
            )
        )

    # Set the aspect ratio
    fig.update_layout(
        autosize=True,
        margin={"r": 0, "t": 0, "l": 0, "b": 0}
    )

    # Save the plot
    if save == True:
        pio.write_image(fig, 'scores_fullscreen.png', width=1920, height=1080)

    # Show the plot
    elif save == False:
        fig.show()

# Function used to generate dfs by borough
def generate_filtered_dfs(df, column_name, values):
  
    filtered_dataframes = []
    
    for value in values:
        filtered_dataframe = df[df[column_name] == value].reset_index(drop=True)
        filtered_dataframes.append(filtered_dataframe)

    return filtered_dataframes # Retruns multiple dfs


# Calculates normalized scores and weighted location score for the given dataframe.
def calculate_scores(df, pop_per_store_weight=.4, pop_per_chain_weight=.4, pop_growth_rate_weight=.2, scaler=MinMaxScaler()):
  
    # Calculate normalized scores
    df['Score | Population per Store'] = np.round(100 * scaler.fit_transform(df[['2023 Population per Store']]), 2)
    df['Score | Population per Chain'] = np.round(100 * scaler.fit_transform(df[['2023 Population per Chain']]), 2)
    df['Score | Population Growth Rate'] = np.round(100 * scaler.fit_transform(df[['2-year Population Growth Rate']]), 2)

    # Calculate weighted location score
    df['Weighted Location Score'] = np.round(pop_per_store_weight * df['Score | Population per Store'] + pop_per_chain_weight * df['Score | Population per Chain'] + pop_growth_rate_weight * df['Score | Population Growth Rate'], 2)

    # Sort the DataFrame by the Weighted Location Score column
    df = df.sort_values('Weighted Location Score', ascending=False)

    # Return df
    return df

## Import Data

- NYC Retail Food Stores CSV (retail food stores licensed by the Department of Agriculture and Markets)

- 2021 NYC Population by Zip Code 

- 2023 NYC Population by Zip Code

- NYC Subway Stations

- GeoJSON File for NY Zip Codes

- GeoJSON File for FRESH Food Stores Zoning Boundaries

In [ ]:
# 1. read csv as store_df
store_df = pd.read_csv('Retail_Food_Stores.csv')

# 2. read csv as pop_2021_zip_df
pop_2021_zip_df = pd.read_csv('2021_ny_zip_populations.csv')

# 3. read csv as pop_2023_zip_df
pop_2023_zip_df = pd.read_csv('2023_ny_zip_populations.csv')

# 4. read csv as subway_df
subway_df = pd.read_csv("DOITT_SUBWAY_STATION_01_13SEPT2010.csv")

Let's look at the store_df with all retail food stores which are licensed by the Department of Agriculture and Markets in the state of New York. Naturally, we will have to filter this dataset to include only grocery stores in New York City since a lot of the rows are not true grocery stores or are outside of the five boroughs.

In [ ]:
store_df

County  License Number Operation Type Establishment Type  \
0       Steuben          756126          Store                JAC   
1        Queens          756125          Store                JAC   
2       Suffolk          756123          Store                JAC   
3      Richmond          756121          Store                JAC   
4        Queens          756120          Store                JAC   
...         ...             ...            ...                ...   
28515    Albany           10086          Store               JABC   
28516    Albany           10070          Store               JABC   
28517    Albany           10066          Store                JAC   
28518    Albany           10056          Store                JAC   
28519    Albany           10008          Store                JAC   

                             Entity Name                 DBA Name  \
0                           7-ELEVEN INC   7 ELEVEN STORE #35111J   
1                           7-ELEVEN INC   7-ELEVEN STORE #35026H   
2                           7-ELEVEN INC   7-ELEVEN STORE #39557H   
3      LA ROCA FUERTE DELI & GROCERY COR  LA ROCA FUERTE DELI & G   
4                      JACKSONS DELI INC            MILLIE'S DELI   
...                                  ...                      ...   
28515     PRICE CHOPPER OPERATING CO INC        PRICE CHOPPER 138   
28516     PRICE CHOPPER OPERATING CO INC        PRICE CHOPPER 133   
28517                  COLUCCIO DOMINICK          NINOS DELI&SUBS   
28518                STEWARTS SHOPS CORP        STEWARTS SHOP 334   
28519                STEWARTS SHOPS CORP        STEWARTS SHOP 105   

      Street Number      Street Name  Address Line 2  Address Line 3  \
0                26          MAIN ST             NaN             NaN   
1            253-02      UNION TPKE.             NaN             NaN   
2               210  MASTIC BEACH RD             NaN             NaN   
3               570      MIDLAND AVE             NaN             NaN   
4             13-01      JACKSON AVE             NaN             NaN   
...             ...              ...             ...             ...   
28515           873    NEW LOUDON RD             NaN             NaN   
28516           911      CENTRAL AVE             NaN             NaN   
28517           718      CENTRAL AVE             NaN             NaN   
28518           219    SAND CREEK RD             NaN             NaN   
28519           624     DELAWARE AVE             NaN             NaN   

                   City State  Zip Code  Square Footage  \
0               ARKPORT    NY     14807               0   
1             GLEN OAKS    NY     11004               0   
2          MASTIC BEACH    NY     11951               0   
3         STATEN ISLAND    NY     10306               0   
4      LONG ISLAND CITY    NY     11101               0   
...                 ...   ...       ...             ...   
28515            LATHAM    NY     12110          150700   
28516            ALBANY    NY     12206           83000   
28517            ALBANY    NY     12206            1500   
28518            ALBANY    NY     12205            1500   
28519            DELMAR    NY     12054            2800   

                     Georeference  NYS Municipal Boundaries  
0      POINT (-77.69553 42.39369)                      31.0  
1      POINT (-73.71744 40.74408)                     196.0  
2      POINT (-72.84823 40.77852)                    1022.0  
3       POINT (-74.09327 40.5724)                     585.0  
4      POINT (-73.94959 40.74412)                     196.0  
...                           ...                       ...  
28515  POINT (-73.75894 42.75422)                     834.0  
28516  POINT (-73.79172 42.68156)                     814.0  
28517  POINT (-73.78593 42.67588)                     814.0  
28518  POINT (-73.79182 42.69767)                     834.0  
28519  POINT (-73.85206 42.61512)                     837.0  

[28520 rows x 16 columns]

Now, let's look at the pop_2021_zip_df which we will use in hand with 2023 figures to compute the population growth rate for each zip code.

In [ ]:
pop_2021_zip_df

Zip Code Population
0         6390         58
1        10001     26,966
2        10002     76,807
3        10003     54,447
4        10004      4,795
...        ...        ...
1770     14898      1,788
1771     14901     15,656
1772     14903      7,184
1773     14904     14,696
1774     14905      8,330

[1775 rows x 2 columns]

Let's also view the pop_2023_zip_df which has the most current population figures by zip code.

In [ ]:
pop_2023_zip_df

zip  population           city    county
0     10001       25026  New York City  New York
1     10002       74363  New York City  New York
2     10003       54671  New York City  New York
3     10004        3310  New York City  New York
4     10005        8664  New York City  New York
...     ...         ...            ...       ...
1616  14898        1772       Woodhull   Steuben
1617  14901       15581         Elmira   Chemung
1618  14903        7186         Elmira   Chemung
1619  14904       15109         Elmira   Chemung
1620  14905        8330         Elmira   Chemung

[1621 rows x 4 columns]

Lastly, let's look at the subway_df which has information about all the subway stops in the city.

In [ ]:
subway_df

URL  OBJECTID                         NAME  \
0    http://web.mta.info/nyct/service/         1                     Astor Pl   
1    http://web.mta.info/nyct/service/         2                     Canal St   
2    http://web.mta.info/nyct/service/         3                      50th St   
3    http://web.mta.info/nyct/service/         4                    Bergen St   
4    http://web.mta.info/nyct/service/         5             Pennsylvania Ave   
..                                 ...       ...                          ...   
468  http://web.mta.info/nyct/service/       469  Coney Island - Stillwell Av   
469  http://web.mta.info/nyct/service/       470       34th St - Hudson Yards   
470  http://web.mta.info/nyct/service/       641                      72nd St   
471  http://web.mta.info/nyct/service/       642                      86th St   
472  http://web.mta.info/nyct/service/       643                      96th St   

                                         the_geom           LINE  \
0    POINT (-73.99106999861966 40.73005400028978)  4-6-6 Express   
1    POINT (-74.00019299927328 40.71880300107709)  4-6-6 Express   
2    POINT (-73.98384899986625 40.76172799961419)            1-2   
3    POINT (-73.97499915116808 40.68086213682956)          2-3-4   
4    POINT (-73.89488591154061 40.66471445143568)            3-4   
..                                            ...            ...   
468   POINT (-73.9812359981396 40.57728100006751)        D-F-N-Q   
469  POINT (-74.00219709442206 40.75544635961596)    7-7 Express   
470  POINT (-73.95836178682246 40.76880251014895)              Q   
471  POINT (-73.95177090964917 40.77786104333163)              Q   
472  POINT (-73.9470660219183 40.784236650177654)              Q   

                                                 NOTES  
0    4 nights, 6-all times, 6 Express-weekdays AM s...  
1    4 nights, 6-all times, 6 Express-weekdays AM s...  
2                                1-all times, 2-nights  
3             4-nights, 3-all other times, 2-all times  
4                          4-nights, 3-all other times  
..                                                 ...  
468                                  D,F,N,Q-all times  
469  7-all times, 7 Express-rush hours AM westbound...  
470                                        Q-all times  
471                                        Q-all times  
472                                        Q-all times  

[473 rows x 6 columns]

## Inputs and Assumptions

The lists below were created based on personal assumptions about what words should and should not be included in filters for grocery stores. Keywords were added/removed manually by iteratively viewing the filtered results. The assumptions can be edited as needed to change the resulting list of grocery stores for the analysis. Fuzzy matching was attempted, but too many intricacies in the store names still existed for filtering to work appropriately.

In [ ]:
# Mapping from county to borough
county_mapping = {
    'New York': 'Manhattan',
    'Kings': 'Brooklyn',
    'Bronx': 'Bronx',
    'Queens': 'Queens',
    'Richmond': 'Staten Island'
}

# Define the wildcard keywords for filtering stores
keywords = [
    "GROCERIES",
    "GROCERY",
    "MARKET",
    "MART",
    "MRKT",
    "MKT",
    "ORGANIC",
    "PANTRY",
    "PRODUCE",
    "SUPER",
    "WHOLESALE"
]

# Stores should not include these wildcard keywords; often niche stores that should not be included
remove_keywords = [
    "@",
    " at ",
    " by ",
    "BAKE",
    "CANDY",
    "CONV",
    "DASHMART",
    "DOLLAR",
    "EXP",
    "FISH",
    "FRUIT",
    "HALLAL",
    "MEAT",
    "MINI",
    "MOBIL",
    "SEAFOOD",
    "SMOKE",
    "SUSH",
    "VEGET"
]

# Specify wildcards accepted for each store; iterative process addded to manually
stores = {
    "ANTILLANA SUPERFOOD MARKET": ["ANTILLANA"],
    "ASSOCIATED SUPERMARKETS": ["ASSOCIATED"],
    "BJS WHOLESALE": ["BJS"],
    "BRAVO SUPERMARKET": ["BRAVO"],
    "BROOKLYN HARVEST MARKET": ["BROOKLYN HARVEST MARKET"],
    "C-TOWN SUPERMARKET": ["C-TOWN", "CTOWN", "C TOWN"],
    "CITY ACRES MARKET": ["CITY ACRES MARKET"],
    "CITY FRESH MARKET": ["CITY FRESH MARKET"],
    "CITARELLA": ["CITARELLA"],
    "COMPARE FOODS": ["COMPARE"],
    "COSTCO WHOLESALE": ["COSTCO"],
    "D'AGOSTINOS": ["AGOSTINO"],
    "EATALY": ["EATALY"],
    "FAIRWAY": ["FAIRWAY"],
    "FINE FARE": ["FINE FARE"],
    "FOOD BAZAAR": ["FOOD BAZAAR"],
    "FOOD EMPORIUM": ["FOOD EMPORIUM"],
    "FOODTOWN": ["FOODTOWN", "FOOD TOWN"],
    "FOOD UNIVERSE": ["FOOD UNIVERSE"],
    "GRISTEDES": ["GRISTEDE"],
    "H MART": ["H-MART", "HMART", "H MART"],
    "HUDSON MARKET": ["HUDSON MARKET"],
    "IDEAL FOOD BASKET": ["IDEAL FOOD BASKET"],
    "KEY FOOD": ["KEY FOOD", "KEYFOOD"],
    "LINCOLN MARKET": ["LINCOLN MARKET"],
    "MET FRESH": ["MET FRESH"],
    "MET FOOD": ["MET FOOD"],
    "MORTON WILLIAMS": ["MORTON WILLIAM"],
    "NET COST MARKET": ["NET COST", "NETCOST"],
    "PIONEER SUPERMARKETS": ["PIONEER"],
    "PREMIUM SUPERMARKET": ["PREMIUM SUPERMARKET"],
    "SHOP FAIR": ["SHOP FAIR"],
    "SUPER FRESH": ["SUPER FRESH", "SUPERFRESH"],
    "TARGET": ["TARGET"],
    "TRADER JOE'S": ["TRADER JOE"],
    "UNION MARKET": ["UNION MARKET"],
    "USA SUPERSTORES": ["USA SUPERSTORE"],
    "WESTSIDE MARKET": ["WESTSIDE", "WEST SIDE"],
    "WHOLE FOODS MARKET": ["WHOLE FOOD"],
    "ZABAR'S": ['ZABARS']
}

We also add two Trader Joe's stores that are missing from the dataset after a manual check. Please see here for info regarding the new stores that opened in Queens in 2021 and 2023. Coordinates for the stores were generated using the Mapquest site. All other Trader Joe's locations were checked and present in the dataset, so no need for additional entries.

In [ ]:
# Add rows for new Trader Joe's after manual spot check
new_rows = [
    {
        'County': 'Queens',
        'License Number': 'N/A',
        'Operation Type': 'Store',
        'Establishment Type': 'A',
        'Entity Name': 'TRADER JOES EAST INC',
        'DBA Name': 'TRADER JOES #578',
        'Street Number': '69-65',
        'Street Name': 'YELLOWSTONE BLVD',
        'Address Line 2': '',
        'Address Line 3': '',
        'City': 'QUEENS',
        'State': 'NY',
        'Zip Code': '11375',
        'Square Footage': 0,
        'Georeference': 'POINT (-73.84861 40.72272)',
        'NYS Municipal Boundaries': 'N/A'
    },
    {
        'County': 'Queens',
        'License Number': 'N/A',
        'Operation Type': 'Store',
        'Establishment Type': 'A',
        'Entity Name': 'TRADER JOES EAST INC',
        'DBA Name': 'TRADER JOES #565',
        'Street Number': '22-43',
        'Street Name': 'JACKSON AVE',
        'Address Line 2': '',
        'Address Line 3': '',
        'City': 'QUEENS',
        'State': 'NY',
        'Zip Code': '11101',
        'Square Footage': 0,
        'Georeference': 'POINT (-73.94607 40.74567)',
        'NYS Municipal Boundaries': 'N/A'
    }
]

# Append the new rows to store_df
store_df = store_df.append(new_rows, ignore_index=True)

## Data Preparation

With the inputs above, we prepare the dataset for our analysis by filtering, dropping rows/columns, creating new columns, etc.

In [ ]:
# Revese stores dictionary for lookup later on
reversed_stores = {value: key for key, values in stores.items() for value in values}

# Create combined list for filter later on
combined_keyword_store = keywords + list(reversed_stores.keys())

# Drop unused columns
columns_to_drop = ['Address Line 2', 'Address Line 3']
store_df = store_df.drop(columns_to_drop, axis=1)

# Drop missing rows for key columns
needed_columns = ['Georeference', 'Street Number', 'DBA Name']
store_df = store_df.dropna(subset=needed_columns)

# Create boroughs column and filter for NYC only
store_df['Borough'] = store_df['County'].map(county_mapping).fillna('Other')
valid_boroughs = list(county_mapping.values())
store_df = store_df[store_df['Borough'].isin(valid_boroughs)]

# Extract lat and long
store_df[['Latitude', 'Longitude']] = store_df['Georeference'].apply(lambda x: pd.Series(extract_coordinates(x)))

# Create address column
store_df['Address'] = store_df['Street Number'] + ' ' + store_df['Street Name'] + ', ' + store_df['City'] + ', ' + store_df['State'] + ' ' + store_df['Zip Code'].astype(str)

# Create pattern string for seaching keywords/stores
pattern = '|'.join([re.escape(word) for word in combined_keyword_store])

# Create a boolean mask indicating rows with column values containing any of the keywords or store wildcards
mask = (store_df['DBA Name'].str.contains(pattern, regex=True, na=False) |
        store_df['Entity Name'].str.contains(pattern, regex=True, na=False))

# Apply the mask to filter the DataFrame
filtered_df = store_df[mask]

# Additional filtering to exclude rows with specific keywords in DBA or entity columns
filtered_df = filtered_df[~(filtered_df['DBA Name'].str.contains('|'.join(remove_keywords), case=False) |
                           filtered_df['Entity Name'].str.contains('|'.join(remove_keywords), case=False))]

# Create a chain column for major chains by mapping DBA column using the reversed stores dictionary with wildcard matching
filtered_df['Chain'] = filtered_df['DBA Name'].apply(lambda x: next((value for key, value in reversed_stores.items() if wildcard_match(key, x)), 'N/A'))

# Create yes or no for large chain derived from chain
filtered_df['Large Chain'] = filtered_df['Chain'].apply(lambda x: 'No' if x == 'N/A' else 'Yes')

# Create new column for type
filtered_df["Type"] = filtered_df["Chain"].apply(lambda x: "SMALL" if x == "N/A" else "TRADER JOE'S" if x == "TRADER JOE'S" else "LARGE CHAIN")

# Create df for large chains only
chain_df = filtered_df[(filtered_df['Large Chain'] == 'Yes')]

# Create df for non-large chains
non_chain_df = filtered_df[(filtered_df['Chain'] == 'N/A')]

# Create df for TJ's only
tj_df = filtered_df[filtered_df['Chain'] == "TRADER JOE'S"]

# Group by zip code and count stores
store_zip_df = filtered_df.groupby(['Zip Code', 'Borough']).size().reset_index(name='Number of Stores')

# Create and merge chain_zip_df
chain_zip_df = chain_df.groupby(['Zip Code']).size().reset_index(name='Number of Chains')
zip_df = store_zip_df.merge(chain_zip_df, on='Zip Code', how = 'outer')

# Merge store_zip_df and pop_2021_zip_df
zip_df = zip_df.merge(pop_2021_zip_df, on='Zip Code', how='outer')

# Replace nan population with zero and convert to float
zip_df['Population'] = zip_df['Population'].fillna(0)
zip_df['Population'] = zip_df['Population'].str.replace(',', '').astype(float)

# Merge pop_2023_zip_df
pop_2023_zip_df = pop_2023_zip_df.drop(['city', 'county'], axis=1)
zip_df = zip_df.merge(pop_2023_zip_df, left_on='Zip Code', right_on='zip', how='outer')

# Rename and drop columns
zip_df = zip_df.rename(columns={'Population': '2021 Population',
                                'population': '2023 Population'})
zip_df = zip_df.drop(['zip'], axis=1)

# Use 2021 populations for missing 2023 populations
zip_df['2023 Population'] = zip_df.apply(lambda row: row['2021 Population'] if pd.isnull(row['2023 Population']) else row['2023 Population'], axis=1)

# Create new columns by zip code and round
zip_df['2-year Population Growth'] = zip_df['2023 Population'] - zip_df['2021 Population']

zip_df['2021 Population per Store'] = np.round(zip_df['2021 Population'] / zip_df['Number of Stores'], 2)
zip_df['2023 Population per Store'] = np.round(zip_df['2023 Population'] / zip_df['Number of Stores'], 2)
zip_df['2-year Population Growth Rate'] = np.round(zip_df['2-year Population Growth'] / zip_df['2021 Population per Store'], 4)
zip_df['Population Per Store Growth'] = np.round(zip_df['2-year Population Growth'] / zip_df['Number of Stores'], 2)

zip_df['2021 Population per Chain'] = np.round(zip_df['2021 Population'] / zip_df['Number of Chains'], 2)
zip_df['2023 Population per Chain'] = np.round(zip_df['2023 Population'] / zip_df['Number of Chains'], 2)
zip_df['2-year Population Growth Rate'] = np.round(zip_df['2-year Population Growth'] / zip_df['2021 Population per Chain'], 4)
zip_df['Population Per Chain Growth'] = np.round(zip_df['2-year Population Growth'] / zip_df['Number of Chains'], 2)

# Replace nan's with zero
zip_df = zip_df.fillna(0)

# Filter for boroughs only
zip_df = zip_df[zip_df['Borough'].isin(county_mapping.values())]

# Subway df
subway_df[['Latitude', 'Longitude']] = subway_df['the_geom'].apply(lambda x: pd.Series(extract_coordinates(x)))

## EDA

Let's now take a look at the resulting dataframes filtered_df representing all grocery stores in the city, tj_df which represents all Trader Joe's stores in the city, and zip_df with a summary of each zip code's store count and population figures.

In [ ]:
filtered_df

County License Number Operation Type Establishment Type  \
3      Richmond         756121          Store                JAC   
14        Kings         756107          Store                JAC   
20        Bronx         756099          Store                JAC   
21        Bronx         756098          Store                JAC   
26        Bronx         756093          Store                JAC   
...         ...            ...            ...                ...   
21990     Bronx         600205          Store                JAC   
21991     Bronx         600187          Store                JAC   
21995     Bronx         600049          Store                JAC   
28520    Queens            N/A          Store                  A   
28521    Queens            N/A          Store                  A   

                             Entity Name                 DBA Name  \
3      LA ROCA FUERTE DELI & GROCERY COR  LA ROCA FUERTE DELI & G   
14                         395 DELI CORP     MUNCH GOURMET MARKET   
20             BOSTON DELI & GROCERY INC    BOSTON DELI & GROCERY   
21             526 S&M DELI GROCERY CORP     526 S&M DELI GROCERY   
26           CANABACOA DELI GROCERY CORP   CANABACOA DELI GROCERY   
...                                  ...                      ...   
21990           CARINO DELI GROCERY CORP           CARINO GROCERY   
21991         ALMANZAR GROCERY&FOOD CORP    ALMANZAR GROCERY&FOOD   
21995                    NANIN FOOD CORP                   C TOWN   
28520               TRADER JOES EAST INC         TRADER JOES #578   
28521               TRADER JOES EAST INC         TRADER JOES #565   

      Street Number             Street Name           City State  ...  \
3               570             MIDLAND AVE  STATEN ISLAND    NY  ...   
14              395  FLATBUSH AVE EXTENSION       BROOKLYN    NY  ...   
20              761          E 169TH STREET          BRONX    NY  ...   
21              526       EAST 183RD STREET          BRONX    NY  ...   
26             1158             GERARD AVE.          BRONX    NY  ...   
...             ...                     ...            ...   ...  ...   
21990           643             E 182ND ST.          BRONX    NY  ...   
21991           854           INTERVALE AVE          BRONX    NY  ...   
21995          2733                 3RD AVE          BRONX    NY  ...   
28520         69-65        YELLOWSTONE BLVD         QUEENS    NY  ...   
28521         22-43             JACKSON AVE         QUEENS    NY  ...   

      Square Footage                Georeference NYS Municipal Boundaries  \
3                  0   POINT (-74.09327 40.5724)                    585.0   
14                 0   POINT (-73.9811 40.68934)                    894.0   
20                 0   POINT (-73.89986 40.8309)                    307.0   
21                 0   POINT (-73.89196 40.8547)                    307.0   
26                 0   POINT (-73.9211 40.83403)                    307.0   
...              ...                         ...                      ...   
21990           1200  POINT (-73.88864 40.85127)                    307.0   
21991           1000  POINT (-73.89562 40.81801)                    307.0   
21995          10000   POINT (-73.9211 40.81425)                    307.0   
28520              0  POINT (-73.84861 40.72272)                      N/A   
28521              0  POINT (-73.94607 40.74567)                      N/A   

             Borough  Latitude  Longitude  \
3      Staten Island  40.57240  -74.09327   
14          Brooklyn  40.68934  -73.98110   
20             Bronx  40.83090  -73.89986   
21             Bronx  40.85470  -73.89196   
26             Bronx  40.83403  -73.92110   
...              ...       ...        ...   
21990          Bronx  40.85127  -73.88864   
21991          Bronx  40.81801  -73.89562   
21995          Bronx  40.81425  -73.92110   
28520         Queens  40.72272  -73.84861   
28521         Queens  40.74567  -73.94607   

                    

In [ ]:
tj_df

County License Number Operation Type Establishment Type  \
2233   New York         751936          Store                  A   
2518      Kings         751378          Store                  A   
7888   New York         739972          Store                  A   
9624   New York         735524          Store                  A   
11817  New York         728784          Store                  A   
11944  New York         728334          Store                  A   
12005     Kings         728061          Store                  A   
12469  New York         725759          Store                  A   
18304  Richmond         641558          Store                  A   
18671    Queens         638571          Store                  A   
19405  New York         628784          Store                  A   
19420  New York         628738          Store                  A   
19628  New York         626894          Store                  A   
21197     Kings         611105          Store                  A   
28520    Queens            N/A          Store                  A   
28521    Queens            N/A          Store                  A   

                 Entity Name           DBA Name Street Number  \
2233    TRADER JOES EAST INC   TRADER JOES #571           405   
2518   TRADER JOE'S EAST INC       TRADER JOE'S           200   
7888    TRADER JOES EAST INC   TRADER JOES #546           436   
9624    TRADER JOES EAST INC   TRADER JOES #538           400   
11817   TRADER JOES EAST INC   TRADER JOES #539           233   
11944   TRADER JOES EAST INC   TRADER JOES #545           670   
12005  TRADER JOE'S EAST INC  TRADER JOE'S #547           445   
12469   TRADER JOES EAST INC   TRADER JOES #544           200   
18304   TRADER JOES EAST INC   TRADER JOES #559          2385   
18671   TRADER JOES EAST INC    TRADER JOES 557         90-30   
19405   TRADER JOES EAST INC   TRADER JOES #542          2073   
19420   TRADER JOES EAST INC   TRADER JOES #543           675   
19628   TRADER JOES EAST INC   TRADER JOES #540           142   
21197   TRADER JOES EAST INC    TRADER JOES 558           130   
28520   TRADER JOES EAST INC   TRADER JOES #578         69-65   
28521   TRADER JOES EAST INC   TRADER JOES #565         22-43   

               Street Name           City State  ... Square Footage  \
2233             E 59TH ST       NEW YORK    NY  ...              0   
2518           KENT AVENUE       BROOKLYN    NY  ...              0   
7888      EAST 14TH STREET       NEW YORK    NY  ...          16000   
9624              GRAND ST       NEW YORK    NY  ...           8000   
11817            SPRING ST       NEW YORK    NY  ...          16000   
11944         COLUMBUS AVE       NEW YORK    NY  ...              0   
12005  GOLD ST SUITE C-020       BROOKLYN    NY  ...              0   
12469            E 32ND ST       NEW YORK    NY  ...          19000   
18304         RICHMOND AVE  STATEN ISLAND    NY  ...          16500   
18671     METROPOLITAN AVE      REGO PARK    NY  ...           9000   
19405             BROADWAY       NEW YORK    NY  ...          14000   
19420              6TH AVE       NEW YORK    NY  ...          21000   
19628            E 14TH ST       NEW YORK    NY  ...          10000   
21197             COURT ST       BROOKLYN    NY  ...          16000   
28520     YELLOWSTONE BLVD         QUEENS    NY  ...              0   
28521          JACKSON AVE         QUEENS    NY  ...              0   

                     Georeference NYS Municipal Boundaries        Borough  \
2233   POINT (-73.96084 40.75914)                    749.0      Manhattan   
2518   POINT (-73.96458 40.71765)                    894.0       Brooklyn   
7888   POINT (-73.98096 40.73066)                    749.0      Manhattan   
9624   POINT (-73.98707 40.71606)                    749.0      Manhattan   
11817  POINT (-74.00489 40.72559)                    749.0      Manhattan   
11944   POINT (-73.96913 40.7907)                    749.0      Manhattan   

In [ ]:
zip_df

Zip Code    Borough  Number of Stores  Number of Chains  2021 Population  \
0      10001  Manhattan              17.0               8.0          26966.0   
1      10002  Manhattan              46.0               6.0          76807.0   
2      10003  Manhattan              25.0               8.0          54447.0   
3      10005  Manhattan               2.0               2.0           8637.0   
4      10007  Manhattan               4.0               3.0           8194.0   
..       ...        ...               ...               ...              ...   
175    11693     Queens               6.0               1.0          14147.0   
176    11694     Queens               8.0               1.0          22432.0   
177    11697     Queens               1.0               0.0           3782.0   
178    11101     Queens               1.0               1.0              0.0   
179    11375     Queens               1.0               1.0              0.0   

     2023 Population  2-year Population Growth  2021 Population per Store  \
0            25026.0                   -1940.0                    1586.24   
1            74363.0                   -2444.0                    1669.72   
2            54671.0                     224.0                    2177.88   
3             8664.0                      27.0                    4318.50   
4             7566.0                    -628.0                    2048.50   
..               ...                       ...                        ...   
175          13029.0                   -1118.0                    2357.83   
176          21258.0                   -1174.0                    2804.00   
177           3527.0                    -255.0                    3782.00   
178              0.0                       0.0                       0.00   
179              0.0                       0.0                       0.00   

     2023 Population per Store  2-year Population Growth Rate  \
0                      1472.12                        -0.5755   
1                      1616.59                        -0.1909   
2                      2186.84                         0.0329   
3                      4332.00                         0.0063   
4                      1891.50                        -0.2299   
..                         ...                            ...   
175                    2171.50                        -0.0790   
176                    2657.25                        -0.0523   
177                    3527.00                         0.0000   
178                       0.00                         0.0000   
179                       0.00                         0.0000   

     Population Per Store Growth  2021 Population per Chain  \
0                        -114.12                    3370.75   
1                         -53.13                   12801.17   
2                           8.96                    6805.88   
3                          13.50                    4318.50   
4                        -157.00                    2731.33   
..                           ...                        ...   
175                      -186.33                   14147.00   
176                      -146.75                   22432.00   
177                      -255.00                       0.00   
178                         0.00                       0.00   
179                         0.00                       0.00   

     2023 Population per Chain  Population Per Chain Growth  
0                      3128.25                      -242.50  
1                     12393.83                      -407.33  
2                      6833.88                        28.00  
3                      4332.00                        13.50  
4                      2522.00                      -209.33  
..                         ...                          ...  
175                   13029.00                     -1118.00  
176                   21258.00                     -1174.00  
177                   

In total, there are 4,631 grocery stores in all five boroughs of New York City; sixteen of which are Trader Joe's locations. Below, we see the most common grocery chains in New York City, with the most frequent being Key Food with 90 locations. Once again, we see Trader Joe's with sixteen locations across the city, making it the thirteenth most common chain by number of stores.

In [ ]:
filtered_df['Chain'].value_counts()

N/A                           4016
KEY FOOD                        90
C-TOWN SUPERMARKET              71
TARGET                          37
FINE FARE                       34
FOODTOWN                        33
BRAVO SUPERMARKET               25
FOOD UNIVERSE                   25
ASSOCIATED SUPERMARKETS         23
MET FOOD                        20
FOOD BAZAAR                     19
GRISTEDES                       18
WHOLE FOODS MARKET              16
TRADER JOE'S                    16
MORTON WILLIAMS                 15
PIONEER SUPERMARKETS            13
H MART                          13
WESTSIDE MARKET                 12
SHOP FAIR                       12
D'AGOSTINOS                     11
IDEAL FOOD BASKET               10
BJS WHOLESALE                   10
FOOD EMPORIUM                    8
MET FRESH                        8
USA SUPERSTORES                  7
UNION MARKET                     7
ANTILLANA SUPERFOOD MARKET       7
NET COST MARKET                  7
COMPARE FOODS       

## Individual Grocery Stores

Let's start by getting an idea of where Trader Joe's sixteen current stores are located across the city. For all the plots below, you can interactively learn more about each store by hovering over the points. You can also pan around the map while zooming in and out.

In [ ]:
make_store_plot(tj_df, "Trader Joe's Stores in NYC", opacity = 1, color = '#EF5350') # Red

Now, let's get an idea of how all 4,631 grocery stores look on a map of New York City. Red points represent Trader Joe's, green points represent other major chains, and blue points represent non-major chain stores. Again, you may want to pan around while zooming in and out to explore further.

In [ ]:
make_store_plot(filtered_df, "All Grocery Stores in NYC", color_column = 'Type', opacity = 1, save=True)
make_store_plot(filtered_df, "All Grocery Stores in NYC", color_column = 'Type', opacity = 1)

## Zip Code Analysis

As one would expect, viewing over 4,000 stores on one plot can be a bit overwhelming, so we aggregate the number of stores by zip code for ease of viewing. Dark red zip codes represent a high number of stores, while lighter colors represent a lower number of stores. You can also see the Trader Joe's locations as red points to get a sense of where their stores already are.

In [ ]:
make_zip_plot(zip_df, 'Number of Stores', tj_df)

What about the number of large chains instead of just stores? As we know, chain grocery stores are typically much larger and attract many more shoppers than small corner grocery stores. Having an idea of where there is a lack of large chains could signal where we should open a new Trader Joe's store.

In [ ]:
make_zip_plot(zip_df, 'Number of Chains', tj_df)

In addition to the number of stores, let's look at the population by zip code, specifically for 2023.

In [ ]:
make_zip_plot(zip_df, '2023 Population', tj_df)

Let's contextualize the plots above by dividing each zip code's population by the number of stores/chains. Ideally, we would want to place a new Trader Joe's store in a zip code that has an already high population-to-store or population-to-chain ratio. As a result, we would expect less competition among grocery stores and more traffic to our new store. Essentially, red zones on the plot represent high-potential opportunities for opening a new Trader Joe's location.

In [ ]:
make_zip_plot(zip_df, '2023 Population per Store', tj_df)
make_zip_plot(zip_df, '2023 Population per Chain', tj_df)

A common theme across the two previous plots is a higher population per store and chain in the boroughs outside of Manhattan. For example, certain zip codes in Staten Island have a population per store near 20k with higher ratios also in Queens. This makes sense because shoppers are more likely to travel long distances to stores because more people have cars outside of Manhattan. Thus, fewer stores are needed in comparison to Manhattan. Let's look at only Manhattan so the scale adjusts and we can see more variation in the map.

In [ ]:
make_zip_plot(zip_df[zip_df['Borough'] == 'Manhattan'], '2023 Population per Store', tj_df[tj_df['Borough'] == 'Manhattan'], center=man_center, zoom=10.5)
make_zip_plot(zip_df[zip_df['Borough'] == 'Manhattan'], '2023 Population per Chain', tj_df[tj_df['Borough'] == 'Manhattan'], center=man_center, zoom=10.5)

As you can see, zip codes within the Upper West Side and Upper East Side and other pockets such as Two Bridges typically have a higher population per store and/or chain. Certain zip codes in Washington Weights and Inwood have a high population per chain, but not per store. Thus, these may be good locations for a new store that we will keep in mind.

Another factor to consider when placing a new Trader Joe's store is making sure the population of a zip code is increasing. If possible, we may want to avoid opening a new location in a zip code where the population is shrinking and thus, there are fewer shoppers. The plot below highlights zip codes in red with high population growth rates from 2021 to 2023.

In [ ]:
make_zip_plot(zip_df, '2-year Population Growth Rate', tj_df)

As you can see in the map above, Williamsburg (zip code: 11211) is clearly a booming neighborhood with a population growth of roughly 4.5% from 2021 to 2023. Most other neighborhoods have remained flat or moderately increased/decreased by less than a percent, likely due to individuals leaving the city during the height of COVID. Thus, Williamsburg may be a good spot for a new Trader Joe's location, even though it has one store already.

## Zip Code Scoring

There are many different plots above that each tells a different story regarding New York City and where might be an optimal location for the next Trader Joe's store. To aggregate these findings, we build a Weighted Location Score that can range from 0-100. The score combines weighted normalized scores from zero to one for 2023 Population per Store, 2023 Population per Chain, and 2-year Population Growth. Currently, the weights are set in the function itself and they can be adjusted if needed:

- pop_per_store_weight = .4

- pop_per_chain_weight = .4

- pop_growth_rate_weight = .2

Let's compute the location scores using the weights above, normalized at the borough level. The choice to normalize the scores by the borough as opposed to altogether was made because expected population per store/chain and overall population growth looks very different in densely populated urban areas such as Manhattan when compared to other more suburban boroughs such as Staten Island. For example, we see and would expect a higher population per store/chain in those suburban areas since people are more likely to get in their car and drive to stores further away, compared to most individuals in Manhattan without a car. As a result, we normalize the values by each borough between zero and one, accounting for variance.

In [ ]:
# Generate dfs for each borough
borough_dfs = generate_filtered_dfs(zip_df, 'Borough', county_mapping.values())
manhattan_df = borough_dfs[0]
brooklyn_df = borough_dfs[1]
bronx_df = borough_dfs[2]
queens_df = borough_dfs[3]
staten_df = borough_dfs[4]

# Calculate location scores
manhattan_df = calculate_scores(manhattan_df)
brooklyn_df = calculate_scores(brooklyn_df)
bronx_df = calculate_scores(bronx_df)
queens_df = calculate_scores(queens_df)
staten_df = calculate_scores(staten_df)

# Combine back to zip_df
zip_df = pd.concat([manhattan_df, brooklyn_df, bronx_df, queens_df, staten_df], ignore_index=True)

# Sort by score 
zip_df = zip_df.sort_values(by="Weighted Location Score", ascending=False)

Below, you see the zip_df including a new column with the overall Weighted Location Score. sorted from highest to lowest. A higher population per store, higher population per chain, and higher population growth rate will all contribute to a higher location score, which can range from zero to one hundred. Although no zip code received a score of one hundred, high location scores represent the “best” potential zip codes for a new Trader Joe’s store, while low location scores represent the “worst” zip codes for a new Trader Joe’s store.

In [ ]:
zip_df

Zip Code        Borough  Number of Stores  Number of Chains  \
84     10475          Bronx               4.0               1.0   
168    10312  Staten Island               3.0               1.0   
0      10044      Manhattan               2.0               1.0   
108    11355         Queens              21.0               1.0   
1      10039      Manhattan              13.0               1.0   
..       ...            ...               ...               ...   
81     11219       Brooklyn              50.0               0.0   
82     11222       Brooklyn              34.0               5.0   
167    11368         Queens              94.0              10.0   
83     11212       Brooklyn              79.0               9.0   
107    10452          Bronx              76.0              12.0   

     2021 Population  2023 Population  2-year Population Growth  \
84           44509.0          43791.0                    -718.0   
168          63935.0          61114.0                   -2821.0   
0            12155.0          12770.0                     615.0   
108          80918.0          81358.0                     440.0   
1            27234.0          27090.0                    -144.0   
..               ...              ...                       ...   
81           93119.0          87812.0                   -5307.0   
82           39669.0          36710.0                   -2959.0   
167         116469.0         108661.0                   -7808.0   
83           78296.0          74037.0                   -4259.0   
107          79838.0          74379.0                   -5459.0   

     2021 Population per Store  2023 Population per Store  \
84                    11127.25                   10947.75   
168                   21311.67                   20371.33   
0                      6077.50                    6385.00   
108                    3853.24                    3874.19   
1                      2094.92                    2083.85   
..                         ...                        ...   
81                     1862.38                    1756.24   
82                     1166.74                    1079.71   
167                    1239.03                    1155.97   
83                      991.09                     937.18   
107                    1050.50                     978.67   

     2-year Population Growth Rate  Population Per Store Growth  \
84                         -0.0161                      -179.50   
168                        -0.0441                      -940.33   
0                           0.0506                       307.50   
108                         0.0054                        20.95   
1                          -0.0053                       -11.08   
..                             ...                          ...   
81                          0.0000                      -106.14   
82                         -0.3730                       -87.03   
167                        -0.6704                       -83.06   
83                         -0.4896                       -53.91   
107                        -0.8205                       -71.83   

     2021 Population per Chain  2023 Population per Chain  \
84                    44509.00                   43791.00   
168                   63935.00                   61114.00   
0                     12155.00                   12770.00   
108                   80918.00                   81358.00   
1                     27234.00                   27090.00   
..                         ...                        ...   
81                        0.00                       0.00   
82                     7933.80                    7342.00   
167                   11646.90                   10866.10   
83                     8699.56                    8226.33   
107                    6653.17                    6198.25   

     Population Per Chain Growth  Score | Population per Store  \
84                       -718.00                        1

With our scores derived, we visualize them on a map of the city, again with existing Trader Joe's stores represented by red points and now included subway stops in black. You can pan around the map and hover over points/zip codes to learn more about the data, including specific score breakdowns.

In [ ]:
make_zip_plot(zip_df, 'Weighted Location Score', tj_df, subway_df)
make_zip_plot(zip_df, 'Weighted Location Score', tj_df, subway_df, save=True)

The maximum score we see is ~98 in the Bronx for zip code 10475. The lowest score we see is ~6 also in the Bronx for zip code 10452. Although subway proximity was not included in the Weighted Location Score, it's helpful to see where the stops are to get an understanding of how accessible a zip code may be for shoppers willing to travel via subway. As we know, the subway is the most popular form of transportation in New York City, and placing a new Trader Joe's store close to a subway increases the number of potential shoppers and thus store revenues.

## FRESH Food Stores Zoning Boundaries

We also look at local tax incentives to help decide on the optimal location for a new Trader Joe's store. We pull data from NYC Open Data for FRESH boundaries which provide tax advantages to new grocery stores opening in certain areas of New York City. According to the dataset description, the benefits are as follows: "FRESH boundaries where zoning and discretionary tax incentives are available for the development, expansion and renovation of full line grocery stores and supermarkets. The FRESH II Text amendment adopted on 12/15/2021 expanded the program to other underserved neighborhoods of the Bronx, Brooklyn, Queens and Staten Island and modified the rules for certification of a FRESH food store." This should not be the primary driver for deciding where to open a new Trader Joe's location (which is why it wasn't included in the weighted location score in the previous section), but it can serve as a potential differentiator for deciding between two locations.

In [ ]:
# Read GeoJSON file
gdf = gpd.read_file('FRESH Food Stores Zoning Boundaries.geojson')

# Create map of FRESH zones
fig = px.choropleth_mapbox(gdf,
                           geojson=gdf.geometry,
                           locations=gdf.index,
                           color_continuous_scale="Viridis",
                           mapbox_style="carto-positron",
                           center=nyc_center,
                           zoom=10.5,
                           opacity=0.25,
                           title ='FRESH Tax-Advantaged Boundaries'
                           )

# Update margins
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

# Save map
pio.write_image(fig, 'fresh_fullscreen.png', width=1920, height=1080)

# Update zoom to 10
fig.update_layout(mapbox=dict(zoom=10))

# Show plot
fig.show()

Above you see that almost the entirety of the Bronx and several across the rest of New York City are eligible for the FRESH tax-advantaged program. We will revisit this map later to help decide on an optimal location.

## Final Recommendation

With the data provided above, I return the top-scoring zip code for each borough. I manually filtered out Manhattan’s highest-scoring zip code in Roosevelt’s Island (10044) since it’s unlikely residents from other zip codes would shop there due to its isolated nature. I also strip out a zip code in Washington Heights (10039) to keep the suggestion for Manhattan further downtown. This is acceptable since the location scores of the top three zip codes in Manhattan were all relatively close in the 60-70 range.

In [ ]:
# Filter out zip code 10044 for Roosevelt Island and 11355 for non-uptown recommendation
rec_df = zip_df[(zip_df['Zip Code'] != 10044) & (zip_df['Zip Code'] != 10039)]

# Calculate top scores for each borough, excluding zip code 10044 and 11355
top_scores = rec_df.groupby('Borough')['Weighted Location Score'].agg('max')

# Merge with the original DataFrame to get all identifying columns
final_df = pd.merge(rec_df, top_scores, on=['Borough', 'Weighted Location Score'], how='inner')

# Show final DataFrame
final_df

Zip Code        Borough  Number of Stores  Number of Chains  \
0    10475          Bronx               4.0               1.0   
1    10312  Staten Island               3.0               1.0   
2    11355         Queens              21.0               1.0   
3    10038      Manhattan              11.0               1.0   
4    11225       Brooklyn              28.0               1.0   

   2021 Population  2023 Population  2-year Population Growth  \
0          44509.0          43791.0                    -718.0   
1          63935.0          61114.0                   -2821.0   
2          80918.0          81358.0                     440.0   
3          23356.0          24205.0                     849.0   
4          59465.0          56072.0                   -3393.0   

   2021 Population per Store  2023 Population per Store  \
0                   11127.25                   10947.75   
1                   21311.67                   20371.33   
2                    3853.24                    3874.19   
3                    2123.27                    2200.45   
4                    2123.75                    2002.57   

   2-year Population Growth Rate  Population Per Store Growth  \
0                        -0.0161                      -179.50   
1                        -0.0441                      -940.33   
2                         0.0054                        20.95   
3                         0.0364                        77.18   
4                        -0.0571                      -121.18   

   2021 Population per Chain  2023 Population per Chain  \
0                    44509.0                    43791.0   
1                    63935.0                    61114.0   
2                    80918.0                    81358.0   
3                    23356.0                    24205.0   
4                    59465.0                    56072.0   

   Population Per Chain Growth  Score | Population per Store  \
0                       -718.0                        100.00   
1                      -2821.0                        100.00   
2                        440.0                         20.51   
3                        849.0                         33.83   
4                      -3393.0                         22.82   

   Score | Population per Chain  Score | Population Growth Rate  \
0                        100.00                           91.66   
1                        100.00                           78.23   
2                        100.00                           91.36   
3                         89.35                           64.15   
4                        100.00                            8.35   

   Weighted Location Score  
0                    98.33  
1                    95.65  
2                    66.48  
3                    62.10  
4                    50.80

My recommendation is to open a new Trader Joe’s store in one of the zip codes above. As expected, there is no right or wrong answer here necessarily, but rather a relative strength of the recommendation. In this case, I would recommend placing the new store somewhere in Manhattan as opposed to one of the other boroughs. This is because nine of Trader Joe’s sixteen existing stores in New York City are located within Manhattan, suggesting it fits their customer base the best.

With a population of roughly 24,000 in 2023 and a two-year population growth of roughly .5%, Two Bridges of downtown Manhattan is an optimal location for a new Trader Joe’s store when compared to other zip codes. It has eleven existing grocery stores, only one of which is a large chain (CTown Supermarkets). Thus, the normalized scores for population per store and chain come in at ~34 and ~89 respectively, with a population growth rate scoring at ~64 – meaning the 10038-zip code represents a high potential opportunity with less competition from existing grocery stores and modest population growth. After applying the weights, we arrive at the weighted location score of ~62, the highest in Manhattan (after filtering out two zip codes) and the overall best recommendation for a new Trader Joe’s location. As you can see from the plot above, the closest Trader Joe’s is in the Lower East Side, so being too close to an existing store is not a concern. Additionally, there are plenty of subway stops that provide easy transportation to the Two Bridges area.

Lastly, Two Bridges is eligible for local tax incentives for new grocery stores within the FRESH zoning tax benefits shared in the previous section.  Even though FRESH zoning boundaries were not included in the weighted location score, it is an important factor that can help us decide between multiple options. Because Two Bridges is eligible for the FRESH tax advantage, it ends up as an even better location for a new Trader Joe’s store. 

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=ff964b57-cd24-4080-af9a-42d6d6727704' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>